In [1]:
import folium
import matplotlib
from matplotlib.pyplot import imread
from matplotlib.colors import Normalize
from folium import raster_layers

In [2]:
image = '/notebooks/resources/gpm/gpm_1d.20190531.tif'

In [22]:
from osgeo import gdal,ogr,osr

def GetExtent(gt,cols,rows):
    ''' Return list of corner coordinates from a geotransform

        @type gt:   C{tuple/list}
        @param gt: geotransform
        @type cols:   C{int}
        @param cols: number of columns in the dataset
        @type rows:   C{int}
        @param rows: number of rows in the dataset
        @rtype:    C{[float,...,float]}
        @return:   coordinates of each corner
    '''
    ext=[]
    xarr=[0,cols]
    yarr=[0,rows]

    for px in xarr:
        for py in yarr:
            x=gt[0]+(px*gt[1])+(py*gt[2])
            y=gt[3]+(px*gt[4])+(py*gt[5])
            ext.append([y,x])
            print (y,x)
        yarr.reverse()
    return ext

def ReprojectCoords(coords,src_srs,tgt_srs):
    ''' Reproject a list of x,y coordinates.

        @type geom:     C{tuple/list}
        @param geom:    List of [[x,y],...[x,y]] coordinates
        @type src_srs:  C{osr.SpatialReference}
        @param src_srs: OSR SpatialReference object
        @type tgt_srs:  C{osr.SpatialReference}
        @param tgt_srs: OSR SpatialReference object
        @rtype:         C{tuple/list}
        @return:        List of transformed [[x,y],...[x,y]] coordinates
    '''
    trans_coords=[]
    transform = osr.CoordinateTransformation( src_srs, tgt_srs)
    for x,y in coords:
        x,y,z = transform.TransformPoint(x,y)
        trans_coords.append([x,y])
    return trans_coords

raster=image
ds=gdal.Open(raster)

gt=ds.GetGeoTransform()
cols = ds.RasterXSize
rows = ds.RasterYSize

ext=GetExtent(gt,cols,rows)
print("ext = " + str(ext))

src_srs=osr.SpatialReference()
src_srs.ImportFromWkt(ds.GetProjection())
# tgt_srs=osr.SpatialReference()
tgt_srs.ImportFromEPSG(3857)
# tgt_srs = src_srs.CloneGeogCS()

geo_ext=ReprojectCoords(ext,src_srs,tgt_srs)
print("geo_ext = " + str(geo_ext))

10.0 -180.0
-60.0 -180.0
-60.0 -30.0
10.0 -30.0
ext = [[10.0, -180.0], [-60.0, -180.0], [-60.0, -30.0], [10.0, -30.0]]
geo_ext = [[0.17453292519943298, -3.141592653589794], [-1.0471975511965979, -3.141592653589794], [-6679169.447596415, -3503549.843504376], [1113194.9079327357, -3503549.843504376]]


In [41]:
m = folium.Map(
      location = [-22, -114]
    , zoom_start = 1
    , control_scale = True 
#     , tiles = 'Stamen Terrain'
#     , crs = 'EPSG4326'
)

data = matplotlib.pyplot.imread(image)

# Image bounds on the map in the form
# [[lat_min, lon_min], [lat_max, lon_max]]
m.add_child(raster_layers.ImageOverlay(
      data
    , opacity = 0.7
#     , bounds = [[-60, -30], [10, -180]]
#     , bounds = [[10, -180], [-60, -30]]
#     , bounds = [[10, -30], [-60, -180]]
    , bounds = [ext[2], ext[0]]
#     , bounds = [[0.17453292519943298, -3.141592653589794], [-6679169.447596415, -3503549.843504376]]
    , mercator_project = True
)
           )

# folium.Marker(
#       ext[2]
#     , popup = '<i>-60, -30</i>'
#     , tooltip = '-60, -30'
# ).add_to(m)

# folium.Marker(
#       ext[0]
#     , popup = '10, -180'
#     , tooltip = '10, -180'
# ).add_to(m)

# folium.Marker(
#       [10, -30]
#     , popup = '<i>10, -30</i>'
#     , tooltip = '10, -30'
# ).add_to(m)

# folium.Marker(
#       [-60, -180]
#     , popup = '<i>-60, -180</i>'
#     , tooltip = '-60, -180'
# ).add_to(m)

folium.Marker(
      [-8399737.89, -20037508.34]
    , popup = '<i>uh...</i>'
    , tooltip = 'uh...'
).add_to(m)



m

In [42]:
vars(m)

{'_children': OrderedDict([('openstreetmap',
               <folium.raster_layers.TileLayer at 0x7f97510933c8>),
              ('image_overlay_029dcef611864ab69a5251c1e152a267',
               <folium.raster_layers.ImageOverlay at 0x7f9750de2978>),
              ('marker_1f4d013e5998403a9052985742ec7dd6',
               <folium.map.Marker at 0x7f9750d68ba8>)]),
 '_env': <jinja2.environment.Environment at 0x7f976fe4cdd8>,
 '_id': '264585f73b94452ca1f725f3a674fe99',
 '_name': 'Map',
 '_parent': <branca.element.Figure at 0x7f9751093898>,
 '_png_image': None,
 'control_scale': True,
 'crs': 'EPSG3857',
 'global_switches': <folium.folium.GlobalSwitches at 0x7f9751093978>,
 'height': (100.0, '%'),
 'left': (0.0, '%'),
 'location': [-22, -114],
 'max_bounds': False,
 'max_lat': 90,
 'max_lon': 180,
 'min_lat': -90,
 'min_lon': -180,
 'no_wrap': False,
 'objects_to_stay_in_front': [],
 'png_enabled': False,
 'position': 'relative',
 'top': (0.0, '%'),
 'width': (100.0, '%'),
 'world_copy_jump'

In [ ]:
print(data)
print(data.shape)
# data = data.transpose()
# print(data)
# print(data.shape)

In [ ]:
!gdalinfo '/notebooks/resources/gpm/gpm_1d.20190531.tif'

In [ ]:
# First: read the geotiff image with GDAL.
from osgeo import gdal, osr

gdal.UseExceptions()

ds = gdal.Open(image)
data = ds.ReadAsArray()
gt = ds.GetGeoTransform()
proj = ds.GetProjection()

inproj = osr.SpatialReference()
inproj.ImportFromWkt(proj)

print('\n\n## ds ##:\n\n' + str(ds))
print('\n\n## data ##:\n\n' + str(data))
print('\n\n## gt ##:\n\n' + str(gt))
print('\n\n## proj ##:\n\n' + str(proj))
print('\n\n## inproj ##:\n\n' + str(inproj))